This notebook computes indicator that had not been previously calculate in a different project.

In [1]:
import xarray as xr
from matplotlib import pyplot as plt
import glob
from xscen.config import CONFIG, load_config
import cartopy.crs as ccrs
import pandas as pd
from matplotlib import pyplot as plt
import xclim as xc
from dask.distributed import Client
from dask.diagnostics import ProgressBar
from pathlib import Path
from xclim.core.calendar import doy_to_days_since, days_since_to_doy,adjust_doy_calendar,convert_calendar
import numpy as np
from itertools import chain


import xscen as xs
from dask.diagnostics import ProgressBar
load_config('paths_pc.yml', verbose=(__name__ == '__main__'), reset=True)
tdd={'xarray_open_kwargs':{'decode_timedelta': False}}

pcat = xs.ProjectCatalog(CONFIG['paths']['project_catalog'])
#pcat_espo = xs.ProjectCatalog(CONFIG['paths']['pcat_espo'])

mod = xs.indicators.load_xclim_module("missing_ind.yml")


INFO:xscen.config:Updated the config with paths_pc.yml.


# PC
careful with tn_min. it is already done.

In [3]:
#portraits
# indicators
sources_hausfather= ['MIROC6','CMCC-ESM2', 'FGOALS-g3', 'ACCESS-CM2', 'ACCESS-ESM1-5', 'MPI-ESM1-2-HR', 'INM-CM5-0',
 'MPI-ESM1-2-LR', 'MRI-ESM2-0', 'NorESM2-LM', 'KACE-1-0-G', 'CNRM-ESM2-1', 'GFDL-ESM4', 'BCC-CSM2-MR']

with Client(n_workers=4, threads_per_worker=3,dashboard_address= 6787, memory_limit="15GB",local_directory= CONFIG['paths']['local_directory'] ):
    ds_dict = pcat_espo.search(processing_level="final", domain='NAM-rdrs',
                               source= sources_hausfather, experiment=['ssp245', 'ssp370']).to_dataset_dict(**tdd)
    
    for i, ds_input in ds_dict.items():       
        for name, ind in mod.iter_indicators():
            # Get the frequency and variable names to check if they are already computed
            outfreq = ind.injected_parameters["freq"].replace("YS", "AS-JAN")
            outnames = [cfatt["var_name"] for cfatt in ind.cf_attrs]
            if (not pcat_espo.exists_in_cat(processing_level='indicators', variable=outnames,
                                             xrfreq=outfreq, id= ds_input.attrs['cat:id']) and 
               name=='heat_wave_total_length_20_30'):            
                ds_input = ds_input.assign(tas=xc.atmos.tg(ds=ds_input))
                out = xs.compute_indicators(
                    ds=ds_input,
                    indicators=[(name, ind)],
                ).popitem()[1]

                #display(out)
                out.attrs['cat:variable']= xs.catalog.parse_from_ds(out, ["variable"])["variable"]
                var=out.attrs['cat:variable'][0]

                if var =='fdd_380':
                    if out['fdd_380'].attrs['calendar']=='360_days':
                        out['fdd_380']=out['fdd_380']/360*365
                    out['fdd_380']=doy_to_days_since(out['fdd_380']) 

                display(out)    
                filename = Path(CONFIG['paths']['indicators'].format(var = var,
                                                                     **xs.utils.get_cat_attrs(out)))

                xs.save_to_zarr(out, filename, mode="o",
                                rechunk={'time':-1}
                               )
                pcat_espo.update_from_ds(ds=out, path=filename)

INFO:distributed.scheduler:State start
INFO:distributed.scheduler:  Scheduler at:     tcp://127.0.0.1:44415
INFO:distributed.scheduler:  dashboard at:            127.0.0.1:6787
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:40090'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:41737'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:39243'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:39512'
/exec/jlavoie/.conda/espo-g/lib/python3.9/contextlib.py:126: UserWarning: Creating scratch directories is taking a surprisingly long time. (1.13s) This is often due to running workers on a network file system. Consider specifying a local-directory to point workers to write scratch data to a local disk.
  next(self.gen)
/exec/jlavoie/.conda/espo-g/lib/python3.9/contextlib.py:126: UserWarning: Creating scratch directories is taking a surprisingly long time. (1.13s) This is often due to running workers on a network file system. Consider


--> The keys in the returned dictionary of datasets are constructed as follows:
	'id.domain.processing_level.xrfreq'


INFO:distributed.utils_perf:full garbage collection released 12.21 MiB from 5573 reference cycles (threshold: 9.54 MiB)
INFO:distributed.core:Event loop was unresponsive in Nanny for 8.94s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 8.94s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 8.95s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 8.95s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Scheduler for 8

INFO:xscen.catalog:An entry exists for: {'processing_level': 'indicators', 'variable': ['fdd_380'], 'xrfreq': 'AS-JUL', 'id': 'CMIP6_ScenarioMIP_CAS_FGOALS-g3_ssp245_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'indicators', 'variable': ['tn_min'], 'xrfreq': 'QS-DEC', 'id': 'CMIP6_ScenarioMIP_CAS_FGOALS-g3_ssp245_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'indicators', 'variable': ['heat_wave_frequency_20_30'], 'xrfreq': 'AS-JAN', 'id': 'CMIP6_ScenarioMIP_CAS_FGOALS-g3_ssp245_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'indicators', 'variable': ['heat_wave_total_length_20_30'], 'xrfreq': 'AS-JAN', 'id': 'CMIP6_ScenarioMIP_CAS_FGOALS-g3_ssp245_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'indicators', 'variable': ['fdd_380'], 'xrfreq': 'AS-JUL', 'id': 'CMIP6_ScenarioMIP_CSIRO-ARCCSS_ACCESS-CM2_ssp245_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exis

INFO:xscen.catalog:An entry exists for: {'processing_level': 'indicators', 'variable': ['heat_wave_frequency_20_30'], 'xrfreq': 'AS-JAN', 'id': 'CMIP6_ScenarioMIP_INM_INM-CM5-0_ssp370_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'indicators', 'variable': ['heat_wave_total_length_20_30'], 'xrfreq': 'AS-JAN', 'id': 'CMIP6_ScenarioMIP_INM_INM-CM5-0_ssp370_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'indicators', 'variable': ['fdd_380'], 'xrfreq': 'AS-JUL', 'id': 'CMIP6_ScenarioMIP_NCC_NorESM2-LM_ssp370_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'indicators', 'variable': ['tn_min'], 'xrfreq': 'QS-DEC', 'id': 'CMIP6_ScenarioMIP_NCC_NorESM2-LM_ssp370_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'indicators', 'variable': ['heat_wave_frequency_20_30'], 'xrfreq': 'AS-JAN', 'id': 'CMIP6_ScenarioMIP_NCC_NorESM2-LM_ssp370_r1i1p1f1_global'}
INFO:xscen.catalog:An

...

<xarray.Dataset>
Dimensions:                       (rlat: 800, rlon: 706, time: 151)
Coordinates:
    lat                           (rlat, rlon) float32 dask.array<chunksize=(50, 50), meta=np.ndarray>
    lon                           (rlat, rlon) float32 dask.array<chunksize=(50, 50), meta=np.ndarray>
  * rlat                          (rlat) float32 -46.17 -46.08 ... 25.65 25.74
  * rlon                          (rlon) float32 324.6 324.7 ... 388.0 388.1
    rotated_pole                  float32 9.969e+36
  * time                          (time) object 1950-01-01 00:00:00 ... 2100-...
Data variables:
    heat_wave_total_length_20_30  (time, rlat, rlon) float64 dask.array<chunksize=(1, 50, 50), meta=np.ndarray>
Attributes: (12/95)
    CMIP6_CV_version:                          cv=6.2.3.0-7-g2019642
    Conventions:                               CF-1.7 CMIP-6.2
    EXPID:                                     CNRM-ESM2-1_historical_r1i1p1f2
    Notes:                                     Regridded on the grid of RDRS ...
    activity_id:                               CMIP
    arpege_minor_version:                      6.3.2
    ...                                        ...
    intake_esm_attrs:date_start:               1950-01-01 00:00
    intake_esm_attrs:date_end:                 2100-12-31 00:00
    intake_esm_attrs:_data_format_:            zarr
    intake_esm_attrs:path:                     /jarre/braun/data/ESPO-G6/fina...
    intake_esm_dataset_key:                    CMIP6_ScenarioMIP_CNRM-CERFACS...
    cat:variable:                              ('heat_wave_total_length_20_30',)

Removing /jarre/scenario/jlavoie/plat-comp/indicators/NAM-rdrs/CMIP6_ScenarioMIP_CNRM-CERFACS_CNRM-ESM2-1_ssp370_r1i1p1f2_global/CMIP6_ScenarioMIP_CNRM-CERFACS_CNRM-ESM2-1_ssp370_r1i1p1f2_global_NAM-rdrs_AS-JAN_heat_wave_total_length_20_30_indicators.zarr/heat_wave_total_length_20_30 to overwrite.


INFO:distributed.core:Event loop was unresponsive in Nanny for 3.32s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 3.36s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 3.43s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 3.46s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Scheduler for 3.49s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeout

INFO:distributed.core:Event loop was unresponsive in Nanny for 3.31s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 3.28s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Scheduler for 3.35s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 3.01s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 3.27s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeout

INFO:distributed.core:Event loop was unresponsive in Nanny for 15.43s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 15.43s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Scheduler for 15.42s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:xscen.catalog:File format not specified. Adding it as 'zarr' based on file name.
INFO:distributed.core:Event loop was unresponsive in Nanny for 7.90s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 7.90s.  This is often caused by 

In [4]:
#portraits
# climatology 
with Client(n_workers=5, threads_per_worker=4,dashboard_address= 6786, memory_limit="6GB",local_directory= CONFIG['paths']['local_directory'] ):
    for name, ind in chain(mod.iter_indicators(), zip(['fdd_380_273'], [mod.fdd_380])):
        ds_dict = pcat_espo.search(processing_level="indicators", domain='NAM-rdrs', variable=name).to_dataset_dict(**tdd)
        for ds_input in ds_dict.values():
            if not pcat_espo.exists_in_cat(processing_level='climatology',
                                           domain='NAM-rdrs',
                                           variable= name,
                                           id= ds_input.attrs['cat:id']) and name=='heat_wave_total_length_20_30':
                periods=[['1951', '2100']]
                ds_mean = xs.climatological_mean(ds=ds_input,
                                                 window= 30,
                                                 interval= 10,
                                                 periods=periods ,
                                                 to_level= 'climatology')


                display(ds_mean)
                filename = Path(CONFIG['paths']['indicators'].format(var=name ,**xs.utils.get_cat_attrs(ds_mean)))
                xs.save_to_zarr(ds_mean, filename, mode="o", rechunk={'time': -1})
                pcat_espo.update_from_ds(ds=ds_mean, path=filename)


INFO:distributed.scheduler:State start
INFO:distributed.scheduler:  Scheduler at:     tcp://127.0.0.1:42258
INFO:distributed.scheduler:  dashboard at:            127.0.0.1:6786
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:46064'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:44008'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:41937'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:44246'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:38816'
INFO:distributed.scheduler:Register worker <WorkerState 'tcp://127.0.0.1:33063', name: 0, status: init, memory: 0, processing: 0>
INFO:distributed.scheduler:Starting worker compute stream, tcp://127.0.0.1:33063
INFO:distributed.core:Starting established connection to tcp://127.0.0.1:33588
INFO:distributed.scheduler:Register worker <WorkerState 'tcp://127.0.0.1:38629', name: 4, status: init, memory: 0, processing: 0>
INFO:distributed.scheduler:Starting worker compu


--> The keys in the returned dictionary of datasets are constructed as follows:
	'id.domain.processing_level.xrfreq'


INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'domain': 'NAM-rdrs', 'variable': 'fdd_380', 'id': 'CMIP6_ScenarioMIP_NIMS-KMA_KACE-1-0-G_ssp245_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'domain': 'NAM-rdrs', 'variable': 'fdd_380', 'id': 'CMIP6_ScenarioMIP_CSIRO-ARCCSS_ACCESS-CM2_ssp245_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'domain': 'NAM-rdrs', 'variable': 'fdd_380', 'id': 'CMIP6_ScenarioMIP_MIROC_MIROC6_ssp245_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'domain': 'NAM-rdrs', 'variable': 'fdd_380', 'id': 'CMIP6_ScenarioMIP_NOAA-GFDL_GFDL-ESM4_ssp245_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'domain': 'NAM-rdrs', 'variable': 'fdd_380', 'id': 'CMIP6_ScenarioMIP_CSIRO_ACCESS-ESM1-5_ssp245_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'proces


--> The keys in the returned dictionary of datasets are constructed as follows:
	'id.domain.processing_level.xrfreq'


INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'domain': 'NAM-rdrs', 'variable': 'tn_min', 'id': 'CMIP6_ScenarioMIP_CSIRO-ARCCSS_ACCESS-CM2_ssp370_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'domain': 'NAM-rdrs', 'variable': 'tn_min', 'id': 'CMIP6_ScenarioMIP_CSIRO-ARCCSS_ACCESS-CM2_ssp245_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'domain': 'NAM-rdrs', 'variable': 'tn_min', 'id': 'CMIP6_ScenarioMIP_MPI-M_MPI-ESM1-2-LR_ssp245_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'domain': 'NAM-rdrs', 'variable': 'tn_min', 'id': 'CMIP6_ScenarioMIP_MPI-M_MPI-ESM1-2-LR_ssp585_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'domain': 'NAM-rdrs', 'variable': 'tn_min', 'id': 'CMIP6_ScenarioMIP_INM_INM-CM5-0_ssp585_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'proces

...

INFO:distributed.core:Event loop was unresponsive in Nanny for 5.41s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Scheduler for 5.70s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 5.70s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 5.70s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 5.54s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeout

<xarray.Dataset>
Dimensions:                       (rlat: 800, rlon: 706, time: 13)
Coordinates:
    lat                           (rlat, rlon) float32 dask.array<chunksize=(50, 50), meta=np.ndarray>
    lon                           (rlat, rlon) float32 dask.array<chunksize=(50, 50), meta=np.ndarray>
  * rlat                          (rlat) float32 -46.17 -46.08 ... 25.65 25.74
  * rlon                          (rlon) float32 324.6 324.7 ... 388.0 388.1
    rotated_pole                  float32 9.969e+36
    horizon                       (time) <U9 '1951-1980' ... '2071-2100'
  * time                          (time) datetime64[ns] 1951-01-01 ... 2071-0...
Data variables:
    heat_wave_total_length_20_30  (time, rlat, rlon) float64 dask.array<chunksize=(13, 50, 50), meta=np.ndarray>
Attributes: (12/89)
    Conventions:                               CF-1.7 CMIP-6.2
    Notes:                                     Regridded on the grid of RDRS ...
    activity_id:                               CMIP
    branch_method:                             standard
    branch_time_in_child:                      0.0
    branch_time_in_parent:                     21915.0
    ...                                        ...
    table_info:                                Creation Date:(30 April 2019) ...
    title:                                     ACCESS-ESM1-5 output prepared ...
    tracking_id:                               hdl:21.14100/585d8ccf-c461-43d...
    variable_id:                               pr
    variant_label:                             r1i1p1f1
    version:                                   1.1.0

INFO:xscen.catalog:File format not specified. Adding it as 'zarr' based on file name.
/exec/jlavoie/.conda/espo-g/lib/python3.9/site-packages/xarray/core/common.py:615: FutureWarning: Updating MultiIndexed coordinate 'time' would corrupt indices for other variables: ['year', 'month', 'day']. This will raise an error in the future. Use `.drop_vars({'month', 'time', 'year', 'day'})` before assigning new coordinate values.


<xarray.Dataset>
Dimensions:                       (rlat: 800, rlon: 706, time: 13)
Coordinates:
    lat                           (rlat, rlon) float32 dask.array<chunksize=(50, 50), meta=np.ndarray>
    lon                           (rlat, rlon) float32 dask.array<chunksize=(50, 50), meta=np.ndarray>
  * rlat                          (rlat) float32 -46.17 -46.08 ... 25.65 25.74
  * rlon                          (rlon) float32 324.6 324.7 ... 388.0 388.1
    rotated_pole                  float32 9.969e+36
    horizon                       (time) <U9 '1951-1980' ... '2071-2100'
  * time                          (time) datetime64[ns] 1951-01-01 ... 2071-0...
Data variables:
    heat_wave_total_length_20_30  (time, rlat, rlon) float64 dask.array<chunksize=(13, 50, 50), meta=np.ndarray>
Attributes: (12/91)
    Conventions:                               CF-1.7 CMIP-6.2
    Notes:                                     Regridded on the grid of RDRS ...
    activity_id:                               CMIP
    branch_method:                             standard
    branch_time_in_child:                      0.0
    branch_time_in_parent:                     0.0
    ...                                        ...
    table_info:                                Creation Date:(05 February 202...
    title:                                     CMCC-ESM2 output prepared for ...
    tracking_id:                               hdl:21.14100/6cd81259-9dd7-4cb...
    variable_id:                               pr
    variant_label:                             r1i1p1f1
    version:                                   1.1.0

INFO:xscen.catalog:File format not specified. Adding it as 'zarr' based on file name.
/tmp/ipykernel_98295/476206283.py:5: UserWarning: There are no datasets to load! Returning an empty dictionary.
INFO:distributed.nanny:Closing Nanny at 'tcp://127.0.0.1:46064'. Reason: nanny-close
INFO:distributed.nanny:Nanny asking worker to close. Reason: nanny-close
INFO:distributed.nanny:Closing Nanny at 'tcp://127.0.0.1:44008'. Reason: nanny-close
INFO:distributed.nanny:Nanny asking worker to close. Reason: nanny-close
INFO:distributed.nanny:Closing Nanny at 'tcp://127.0.0.1:41937'. Reason: nanny-close
INFO:distributed.nanny:Nanny asking worker to close. Reason: nanny-close
INFO:distributed.nanny:Closing Nanny at 'tcp://127.0.0.1:44246'. Reason: nanny-close
INFO:distributed.nanny:Nanny asking worker to close. Reason: nanny-close
INFO:distributed.nanny:Closing Nanny at 'tcp://127.0.0.1:38816'. Reason: nanny-close
INFO:distributed.nanny:Nanny asking worker to close. Reason: nanny-close
INFO:distrib

In [5]:
# delta
with Client(n_workers=5, threads_per_worker=4,dashboard_address= 6786, memory_limit="6GB",local_directory= CONFIG['paths']['local_directory'] ):
    for name, ind in chain(mod.iter_indicators(), zip(['fdd_380_273'], [mod.fdd_380])):
        ds_dict = pcat_espo.search(processing_level="climatology", domain='NAM-rdrs', variable=name).to_dataset_dict(**tdd)
        for ds_input in ds_dict.values():
            if not pcat_espo.exists_in_cat(processing_level='abs-delta-1991-2020',
                                           domain='NAM-rdrs',
                                           variable=f"{name}_delta_1991_2020",
                                           id= ds_input.attrs['cat:id']) and name=='heat_wave_total_length_20_30':

                ds_delta = xs.aggregate.compute_deltas(ds=ds_input,
                                                       reference_horizon= "1991-2020",
                                                       kind="+",
                                                       to_level='abs-delta-1991-2020')
                display(ds_delta)
                var =  [x for x in ds_delta.data_vars][0]
                filename = Path(CONFIG['paths']['indicators'].format(var=var,**xs.utils.get_cat_attrs(ds_delta)))
                xs.save_to_zarr(ds_delta, filename, mode="o")
                pcat_espo.update_from_ds(ds=ds_delta, path=filename)

INFO:distributed.scheduler:State start
INFO:distributed.scheduler:  Scheduler at:     tcp://127.0.0.1:45849
INFO:distributed.scheduler:  dashboard at:            127.0.0.1:6786
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:33066'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:35503'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:35077'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:33405'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:41870'
INFO:distributed.scheduler:Register worker <WorkerState 'tcp://127.0.0.1:45467', name: 1, status: init, memory: 0, processing: 0>
INFO:distributed.scheduler:Starting worker compute stream, tcp://127.0.0.1:45467
INFO:distributed.core:Starting established connection to tcp://127.0.0.1:34926
INFO:distributed.scheduler:Register worker <WorkerState 'tcp://127.0.0.1:39751', name: 0, status: init, memory: 0, processing: 0>
INFO:distributed.scheduler:Starting worker compu


--> The keys in the returned dictionary of datasets are constructed as follows:
	'id.domain.processing_level.xrfreq'



--> The keys in the returned dictionary of datasets are constructed as follows:
	'id.domain.processing_level.xrfreq'


INFO:xscen.catalog:An entry exists for: {'processing_level': 'abs-delta-1991-2020', 'domain': 'NAM-rdrs', 'variable': 'tn_min_delta_1991_2020', 'id': 'CMIP6_ScenarioMIP_CNRM-CERFACS_CNRM-ESM2-1_ssp370_r1i1p1f2_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'abs-delta-1991-2020', 'domain': 'NAM-rdrs', 'variable': 'tn_min_delta_1991_2020', 'id': 'CMIP6_ScenarioMIP_MIROC_MIROC6_ssp370_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'abs-delta-1991-2020', 'domain': 'NAM-rdrs', 'variable': 'tn_min_delta_1991_2020', 'id': 'CMIP6_ScenarioMIP_NCC_NorESM2-LM_ssp370_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'abs-delta-1991-2020', 'domain': 'NAM-rdrs', 'variable': 'tn_min_delta_1991_2020', 'id': 'CMIP6_ScenarioMIP_CAS_FGOALS-g3_ssp585_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'abs-delta-1991-2020', 'domain': 'NAM-rdrs', 'variable': 'tn_min_delta_1991_2020', 'id': 'CMIP6_

INFO:xscen.catalog:An entry exists for: {'processing_level': 'abs-delta-1991-2020', 'domain': 'NAM-rdrs', 'variable': 'tn_min_delta_1991_2020', 'id': 'CMIP6_ScenarioMIP_MPI-M_MPI-ESM1-2-LR_ssp245_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'abs-delta-1991-2020', 'domain': 'NAM-rdrs', 'variable': 'tn_min_delta_1991_2020', 'id': 'CMIP6_ScenarioMIP_CNRM-CERFACS_CNRM-ESM2-1_ssp585_r1i1p1f2_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'abs-delta-1991-2020', 'domain': 'NAM-rdrs', 'variable': 'tn_min_delta_1991_2020', 'id': 'CMIP6_ScenarioMIP_NUIST_NESM3_ssp245_r1i1p1f1_global'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'abs-delta-1991-2020', 'domain': 'NAM-rdrs', 'variable': 'tn_min_delta_1991_2020', 'id': 'CMIP6_ScenarioMIP_NOAA-GFDL_GFDL-ESM4_ssp245_r1i1p1f1_global'}


...

INFO:xscen.catalog:File format not specified. Adding it as 'zarr' based on file name.
/exec/jlavoie/.conda/espo-g/lib/python3.9/site-packages/xscen/aggregate.py:283: FutureWarning: Updating MultiIndexed coordinate 'time' would corrupt indices for other variables: ['year', 'month', 'day']. This will raise an error in the future. Use `.drop_vars({'month', 'time', 'year', 'day'})` before assigning new coordinate values.


<xarray.Dataset>
Dimensions:                                       (time: 13, rlat: 800,
                                                   rlon: 706)
Coordinates:
    rotated_pole                                  float32 9.969e+36
    horizon                                       (time) <U9 dask.array<chunksize=(13,), meta=np.ndarray>
    lon                                           (rlat, rlon) float32 dask.array<chunksize=(50, 50), meta=np.ndarray>
  * rlat                                          (rlat) float32 -46.17 ... 2...
  * rlon                                          (rlon) float32 324.6 ... 388.1
    lat                                           (rlat, rlon) float32 dask.array<chunksize=(50, 50), meta=np.ndarray>
  * time                                          (time) datetime64[ns] 1951-...
Data variables:
    heat_wave_total_length_20_30_delta_1991_2020  (time, rlat, rlon) float64 dask.array<chunksize=(13, 50, 50), meta=np.ndarray>
Attributes: (12/89)
    Conventions:                               CF-1.7 CMIP-6.2
    Notes:                                     Regridded on the grid of RDRS ...
    activity_id:                               CMIP
    branch_method:                             standard
    branch_time_in_child:                      0.0
    branch_time_in_parent:                     0.0
    ...                                        ...
    table_info:                                Creation Date:(30 April 2019) ...
    title:                                     ACCESS-CM2 output prepared for...
    tracking_id:                               hdl:21.14100/27a2a033-bc7e-45f...
    variable_id:                               pr
    variant_label:                             r1i1p1f1
    version:                                   1.1.0

INFO:distributed.core:Event loop was unresponsive in Nanny for 4.68s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 4.68s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Scheduler for 4.45s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 4.45s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 4.45s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeout

<xarray.Dataset>
Dimensions:                                       (time: 13, rlat: 800,
                                                   rlon: 706)
Coordinates:
    rotated_pole                                  float32 9.969e+36
    horizon                                       (time) <U9 dask.array<chunksize=(13,), meta=np.ndarray>
    lon                                           (rlat, rlon) float32 dask.array<chunksize=(50, 50), meta=np.ndarray>
  * rlat                                          (rlat) float32 -46.17 ... 2...
  * rlon                                          (rlon) float32 324.6 ... 388.1
    lat                                           (rlat, rlon) float32 dask.array<chunksize=(50, 50), meta=np.ndarray>
  * time                                          (time) datetime64[ns] 1951-...
Data variables:
    heat_wave_total_length_20_30_delta_1991_2020  (time, rlat, rlon) float64 dask.array<chunksize=(13, 50, 50), meta=np.ndarray>
Attributes: (12/90)
    Conventions:                               CF-1.7 CMIP-6.2
    Notes:                                     Regridded on the grid of RDRS ...
    activity_id:                               CMIP
    branch_method:                             standard
    branch_time_in_child:                      0.0
    branch_time_in_parent:                     0.0
    ...                                        ...
    table_info:                                Creation Date:(09 May 2019) MD...
    title:                                     MPI-ESM1-2-HR output prepared ...
    tracking_id:                               hdl:21.14100/6585ffe8-eb3a-42b...
    variable_id:                               pr
    variant_label:                             r1i1p1f1
    version:                                   1.1.0

INFO:xscen.catalog:File format not specified. Adding it as 'zarr' based on file name.
/tmp/ipykernel_98295/3910274419.py:4: UserWarning: There are no datasets to load! Returning an empty dictionary.
INFO:distributed.nanny:Closing Nanny at 'tcp://127.0.0.1:33066'. Reason: nanny-close
INFO:distributed.nanny:Nanny asking worker to close. Reason: nanny-close
INFO:distributed.nanny:Closing Nanny at 'tcp://127.0.0.1:35503'. Reason: nanny-close
INFO:distributed.nanny:Nanny asking worker to close. Reason: nanny-close
INFO:distributed.nanny:Closing Nanny at 'tcp://127.0.0.1:35077'. Reason: nanny-close
INFO:distributed.nanny:Nanny asking worker to close. Reason: nanny-close
INFO:distributed.nanny:Closing Nanny at 'tcp://127.0.0.1:33405'. Reason: nanny-close
INFO:distributed.nanny:Nanny asking worker to close. Reason: nanny-close
INFO:distributed.nanny:Closing Nanny at 'tcp://127.0.0.1:41870'. Reason: nanny-close
INFO:distributed.nanny:Nanny asking worker to close. Reason: nanny-close
INFO:distri

In [6]:
# ensemble

# one ensemble (file) per level, per xrfreq, per variable, per experiment
for bias_adjust_project in ['ESPO-G6']:
    for processing_level in ['indicators','climatology','abs-delta-1991-2020']:
        for experiment in ['ssp245', 'ssp370']:
            for name, ind in chain(mod.iter_indicators(), zip(['fdd_380_273'], [mod.fdd_380])):
                

                if not pcat_espo.exists_in_cat(
                        processing_level= f'ensemble-{processing_level}',
                        experiment=experiment,
                        bias_adjust_project=bias_adjust_project,
                        variable=[f"{name}_p50", f"{name}_delta_1991_2020_p50"],
                ) and name=='heat_wave_total_length_20_30':
                    with ProgressBar():
                        ind_dict = pcat_espo.search( processing_level=processing_level,
                                                                variable=[name, f"{name}_delta_1991_2020"],
                                                                experiment=experiment,
                                                                bias_adjust_project=bias_adjust_project,
                                                                ).to_dataset_dict(
                                            #**tdd
                                            **{'xarray_open_kwargs':{'decode_timedelta': False, 'chunks':{'time':-1}}}
                                        )
                        ens = xs.ensembles.ensemble_stats(
                            datasets=ind_dict,
                            to_level= f'ensemble-{processing_level}',
                            statistics={'ensemble_percentiles':{'split': True}},
                            common_attrs_only= True,
                            create_kwargs={'chunks':{'horizon': -1}},
                        )

                        ens.attrs['cat:variable']= xs.catalog.parse_from_ds(ens, ["variable"])["variable"]
                        display(ens)

                        filename = Path(CONFIG['paths']['indicators'].format(var = name,
                                                                             **xs.utils.get_cat_attrs(ens)))
                        xs.save_to_zarr(ens, filename, mode="o", rechunk={'time':-1})
                        pcat_espo.update_from_ds(ds=ens, path=filename)

INFO:xscen.catalog:An entry exists for: {'processing_level': 'ensemble-indicators', 'experiment': 'ssp245', 'bias_adjust_project': 'ESPO-G6', 'variable': ['fdd_380_p50', 'fdd_380_delta_1991_2020_p50']}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'ensemble-indicators', 'experiment': 'ssp245', 'bias_adjust_project': 'ESPO-G6', 'variable': ['tn_min_p50', 'tn_min_delta_1991_2020_p50']}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'ensemble-indicators', 'experiment': 'ssp245', 'bias_adjust_project': 'ESPO-G6', 'variable': ['heat_wave_frequency_20_30_p50', 'heat_wave_frequency_20_30_delta_1991_2020_p50']}



--> The keys in the returned dictionary of datasets are constructed as follows:
	'id.domain.processing_level.xrfreq'
[                                        ] | 0% Completed | 238.41 us

[########################################] | 100% Completed | 2.42 ss


INFO:xscen.ensembles:Creating ensemble with 14 simulations and calculating ensemble_percentiles.


<xarray.Dataset>
Dimensions:                           (time: 151, rlat: 800, rlon: 706)
Coordinates:
    lat                               (rlat, rlon) float32 dask.array<chunksize=(800, 706), meta=np.ndarray>
    lon                               (rlat, rlon) float32 dask.array<chunksize=(800, 706), meta=np.ndarray>
  * rlat                              (rlat) float32 -46.17 -46.08 ... 25.74
  * rlon                              (rlon) float32 324.6 324.7 ... 388.0 388.1
    rotated_pole                      float32 9.969e+36
  * time                              (time) object 1950-01-01 00:00:00 ... 2...
Data variables:
    heat_wave_total_length_20_30_p10  (time, rlat, rlon) float64 dask.array<chunksize=(151, 50, 50), meta=np.ndarray>
    heat_wave_total_length_20_30_p50  (time, rlat, rlon) float64 dask.array<chunksize=(151, 50, 50), meta=np.ndarray>
    heat_wave_total_length_20_30_p90  (time, rlat, rlon) float64 dask.array<chunksize=(151, 50, 50), meta=np.ndarray>
Attributes: (12/50)
    Notes:                                     Regridded on the grid of RDRS ...
    activity_id:                               CMIP
    branch_time_in_child:                      0.0
    cat:_data_format_:                         zarr
    cat:activity:                              ScenarioMIP
    cat:bias_adjust_institution:               Ouranos
    ...                                        ...
    sub_experiment_id:                         none
    table_id:                                  day
    variable_id:                               pr
    version:                                   1.1.0
    cat:id:                                    ESPO-G6_CMIP6_ScenarioMIP_ssp2...
    ensemble_size:                             14

...


--> The keys in the returned dictionary of datasets are constructed as follows:
	'id.domain.processing_level.xrfreq'
[                                        ] | 0% Completed | 110.26 ms

[########################################] | 100% Completed | 343.59 ms


INFO:xscen.ensembles:Creating ensemble with 14 simulations and calculating ensemble_percentiles.


<xarray.Dataset>
Dimensions:                                           (time: 13, rlat: 800,
                                                       rlon: 706)
Coordinates:
    horizon                                           (time) <U9 dask.array<chunksize=(13,), meta=np.ndarray>
    lat                                               (rlat, rlon) float32 dask.array<chunksize=(800, 706), meta=np.ndarray>
    lon                                               (rlat, rlon) float32 dask.array<chunksize=(800, 706), meta=np.ndarray>
  * rlat                                              (rlat) float32 -46.17 ....
  * rlon                                              (rlon) float32 324.6 .....
    rotated_pole                                      float32 9.969e+36
  * time                                              (time) datetime64[ns] 1...
Data variables:
    heat_wave_total_length_20_30_delta_1991_2020_p10  (time, rlat, rlon) float64 dask.array<chunksize=(13, 50, 50), meta=np.ndarray>
    heat_wave_total_length_20_30_delta_1991_2020_p50  (time, rlat, rlon) float64 dask.array<chunksize=(13, 50, 50), meta=np.ndarray>
    heat_wave_total_length_20_30_delta_1991_2020_p90  (time, rlat, rlon) float64 dask.array<chunksize=(13, 50, 50), meta=np.ndarray>
Attributes: (12/52)
    Notes:                                     Regridded on the grid of RDRS ...
    activity_id:                               CMIP
    branch_time_in_child:                      0.0
    cat:_data_format_:                         zarr
    cat:activity:                              ScenarioMIP
    cat:bias_adjust_institution:               Ouranos
    ...                                        ...
    sub_experiment_id:                         none
    table_id:                                  day
    variable_id:                               pr
    version:                                   1.1.0
    cat:id:                                    ESPO-G6_CMIP6_ScenarioMIP_ssp3...
    ensemble_size:                             14

/exec/jlavoie/.conda/espo-g/lib/python3.9/site-packages/xclim/core/utils.py:462: RuntimeWarning: All-NaN slice encountered
INFO:xscen.catalog:File format not specified. Adding it as 'zarr' based on file name.


# CDCA

In [2]:
# climate data
# indicators
models_pcic =['ACCESS-CM2', 'CanESM5', 'CNRM-CM6-1', 'EC-Earth3-Veg', 'HadGEM3-GC31-LL', 'IPSL-CM6A-LR', 'MIROC6',
'MPI-ESM1-2-LR', 'NorESM2-MM', 'ACCESS-ESM1-5', 'CMCC-ESM2', 'CNRM-ESM2-1', 'FGOALS-g3', 'INM-CM4-8',
'KACE-1-0-G', 'MIROC-ES2L', 'MRI-ESM2-0', 'TaiESM1', 'BCC-CSM2-MR', 'EC-Earth3', 'GFDL-ESM4', 'INM-CM5-0', 
'KIOST-ESM', 'MPI-ESM1-2-HR', 'NorESM2-LM', 'UKESM1-0-LL']
with Client(n_workers=4, threads_per_worker=4,dashboard_address= 40967, memory_limit="6GB",local_directory= CONFIG['paths']['local_directory'] ):
    for exp in['ssp245', 'ssp585']:
        for m in models_pcic:
            f= glob.glob(f'/tank/jlavoie/ccdp/input/PCIC/day_BCCAQv2+ANUSPLIN300_{m}_historical+{exp}_*.zarr')[0]
            for name, ind in mod.iter_indicators():
                # Get the frequency and variable names to check if they are already computed
                outfreq = ind.injected_parameters["freq"].replace("YS", "AS-JAN")
                outnames = [cfatt["var_name"] for cfatt in ind.cf_attrs]
                if ((not pcat.exists_in_cat(processing_level='indicators',
                                          variable=outnames,
                                          xrfreq=outfreq,
                                          source=m,
                                          experiment=exp,
                                          bias_adjust_project='climatedata')) 
                    and name!='tn_min' ): # already done tn_min MS
                    ds_input= xr.open_zarr(f, decode_timedelta=False)
                    out = xs.compute_indicators(
                        ds=ds_input,
                        indicators=[(name, ind)],
                    ).popitem()[1]

                    #display(out)
                    out.attrs['cat:variable']= xs.catalog.parse_from_ds(out, ["variable"])["variable"]
                    var=out.attrs['cat:variable'][0]
                    out.attrs['cat:domain']='PCIC-CAN'
                    out.attrs['cat:xrfreq']=outfreq
                    out.attrs['cat:type']='simulation'
                    out.attrs['cat:bias_adjust_institution']= 'PCIC'
                    out.attrs['cat:bias_adjust_project']='climatedata'
                    out.attrs['cat:mip_era']= 'CMIP6'
                    out.attrs['cat:activity']= 'ScenarioMIP'
                    out.attrs['cat:experiment']= exp
                    out.attrs['cat:domain']='CAN-PCIC'
                    out.attrs['cat:source']=m
                    out.attrs['cat:instution']=out.attrs['GCM__institution_id']
                    out.attrs['cat:id']=xs.catalog.generate_id(out).iloc[0]

                    if var =='fdd_380':
                        if out['fdd_380'].attrs['calendar']=='360_days':
                            out['fdd_380']=out['fdd_380']/360*365
                        out['fdd_380']=doy_to_days_since(out['fdd_380']) 
                    display(out)
                    filename = Path(CONFIG['paths']['indicators'].format(var = var,
                                                                         **xs.utils.get_cat_attrs(out)))
                    xs.save_to_zarr(out, filename, mode="o",rechunk={'time': -1})
                    pcat.update_from_ds(ds=out, path=filename)

INFO:distributed.scheduler:State start
INFO:distributed.scheduler:  Scheduler at:     tcp://127.0.0.1:36602
INFO:distributed.scheduler:  dashboard at:           127.0.0.1:40967
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:37027'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:43119'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:43717'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:45702'
INFO:distributed.scheduler:Register worker <WorkerState 'tcp://127.0.0.1:44686', name: 3, status: init, memory: 0, processing: 0>
INFO:distributed.scheduler:Starting worker compute stream, tcp://127.0.0.1:44686
INFO:distributed.core:Starting established connection to tcp://127.0.0.1:41230
INFO:distributed.scheduler:Register worker <WorkerState 'tcp://127.0.0.1:34686', name: 2, status: init, memory: 0, processing: 0>
INFO:distributed.scheduler:Starting worker compute stream, tcp://127.0.0.1:34686
INFO:distributed.core:Starting establi

INFO:xscen.catalog:An entry exists for: {'processing_level': 'indicators', 'variable': ['fdd_380'], 'xrfreq': 'AS-JUL', 'source': 'CMCC-ESM2', 'experiment': 'ssp245', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'indicators', 'variable': ['dlyfrzthw'], 'xrfreq': 'AS-JAN', 'source': 'CMCC-ESM2', 'experiment': 'ssp245', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'indicators', 'variable': ['heat_wave_total_length_20_30'], 'xrfreq': 'AS-JAN', 'source': 'CMCC-ESM2', 'experiment': 'ssp245', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'indicators', 'variable': ['fdd_380'], 'xrfreq': 'AS-JUL', 'source': 'CNRM-ESM2-1', 'experiment': 'ssp245', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'indicators', 'variable': ['dlyfrzthw'], 'xrfreq': 'AS-JAN', 'source': 'CNRM-ESM2-1', 'experim

INFO:xscen.catalog:An entry exists for: {'processing_level': 'indicators', 'variable': ['fdd_380'], 'xrfreq': 'AS-JUL', 'source': 'MPI-ESM1-2-HR', 'experiment': 'ssp245', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'indicators', 'variable': ['dlyfrzthw'], 'xrfreq': 'AS-JAN', 'source': 'MPI-ESM1-2-HR', 'experiment': 'ssp245', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'indicators', 'variable': ['heat_wave_total_length_20_30'], 'xrfreq': 'AS-JAN', 'source': 'MPI-ESM1-2-HR', 'experiment': 'ssp245', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'indicators', 'variable': ['fdd_380'], 'xrfreq': 'AS-JUL', 'source': 'NorESM2-LM', 'experiment': 'ssp245', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'indicators', 'variable': ['dlyfrzthw'], 'xrfreq': 'AS-JAN', 'source': 'NorESM2-LM'

<xarray.Dataset>
Dimensions:    (lat: 510, lon: 1068, time: 151)
Coordinates:
  * lat        (lat) float64 41.04 41.12 41.21 41.29 ... 83.21 83.29 83.37 83.46
  * lon        (lon) float64 -141.0 -140.9 -140.8 ... -52.21 -52.13 -52.04
  * time       (time) datetime64[ns] 1950-01-01 1951-01-01 ... 2100-01-01
Data variables:
    dlyfrzthw  (time, lat, lon) float64 dask.array<chunksize=(1, 64, 64), meta=np.ndarray>
Attributes: (12/58)
    Conventions:                  CF-1.7 CMIP-6.2
    GCM__branch_method:           standard
    GCM__data_specs_version:      01.00.30
    GCM__experiment:              historical,ssp585
    GCM__experiment_id:           historical,ssp585
    GCM__forcing_index:           1
    ...                           ...
    cat:mip_era:                  CMIP6
    cat:activity:                 ScenarioMIP
    cat:experiment:               ssp585
    cat:source:                   ACCESS-ESM1-5
    cat:instution:                CSIRO
    cat:id:                       climatedata_CMIP6_ScenarioMIP_ACCESS-ESM1-5...

Removing /jarre/scenario/jlavoie/plat-comp/indicators/CAN-PCIC/climatedata_CMIP6_ScenarioMIP_ACCESS-ESM1-5_ssp585_CAN-PCIC/climatedata_CMIP6_ScenarioMIP_ACCESS-ESM1-5_ssp585_CAN-PCIC_CAN-PCIC_AS-JAN_dlyfrzthw_indicators.zarr/dlyfrzthw to overwrite.


...

INFO:distributed.core:Event loop was unresponsive in Nanny for 5.16s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Scheduler for 5.18s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 5.18s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 5.24s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 5.29s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeout

INFO:distributed.core:Event loop was unresponsive in Scheduler for 8.41s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 8.79s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 8.76s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 8.77s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 9.23s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeout

INFO:distributed.core:Event loop was unresponsive in Nanny for 8.36s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 9.99s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 10.00s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 10.05s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 10.10s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts

INFO:distributed.core:Event loop was unresponsive in Nanny for 8.11s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 8.17s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Scheduler for 8.23s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 3.45s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 3.53s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeout

INFO:distributed.core:Event loop was unresponsive in Nanny for 11.77s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Scheduler for 11.77s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 305.65s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 305.65s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause timeouts and instability.
INFO:distributed.core:Event loop was unresponsive in Nanny for 305.65s.  This is often caused by long-running GIL-holding functions or moving large chunks of data. This can cause

In [3]:
# climatology 
with Client(n_workers=5, threads_per_worker=4,dashboard_address= 6787, memory_limit="6GB",local_directory= CONFIG['paths']['local_directory'] ):
    for name, ind in chain(mod.iter_indicators(), zip(['fdd_380_273'], [mod.fdd_380])):
        ds_dict = pcat.search(processing_level="indicators", variable=name,
                              bias_adjust_project='climatedata').to_dataset_dict(**tdd)
        for ds_input in ds_dict.values():
            if not pcat.exists_in_cat(processing_level='climatology', variable=name,
                                      experiment=ds_input.attrs['cat:experiment'],
                                      id= ds_input.attrs['cat:id'],bias_adjust_project='climatedata'):
                periods= [['1951', '2100']]
                ds_mean = xs.climatological_mean(ds=ds_input,
                                                 window= 30,
                                                 interval= 10,
                                                 periods=periods ,
                                                 to_level= 'climatology')


                display(ds_mean)
                var = ds_mean.attrs['cat:variable'][0]
                filename = Path(CONFIG['paths']['indicators'].format(var=var ,**xs.utils.get_cat_attrs(ds_mean)))
                xs.save_to_zarr(ds_mean, filename, mode="o", rechunk={'time': -1})
                pcat.update_from_ds(ds=ds_mean, path=filename)


/exec/jlavoie/.conda/espo-g/lib/python3.9/site-packages/distributed/node.py:182: UserWarning: Port 6787 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 36926 instead
INFO:distributed.scheduler:State start
INFO:distributed.scheduler:  Scheduler at:     tcp://127.0.0.1:43939
INFO:distributed.scheduler:  dashboard at:           127.0.0.1:36926
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:42241'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:35753'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:43291'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:34607'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:33076'
INFO:distributed.scheduler:Register worker <WorkerState 'tcp://127.0.0.1:42918', name: 0, status: init, memory: 0, processing: 0>
INFO:distributed.scheduler:Starting worker compute stream, tcp://127.0.0.1:42918
INFO:distributed.core:Starting established c


--> The keys in the returned dictionary of datasets are constructed as follows:
	'id.domain.processing_level.xrfreq'


INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'fdd_380', 'experiment': 'ssp245', 'id': 'climatedata_CMIP6_ScenarioMIP_MRI-ESM2-0_ssp245_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'fdd_380', 'experiment': 'ssp245', 'id': 'climatedata_CMIP6_ScenarioMIP_EC-Earth3-Veg_ssp245_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'fdd_380', 'experiment': 'ssp585', 'id': 'climatedata_CMIP6_ScenarioMIP_TaiESM1_ssp585_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'fdd_380', 'experiment': 'ssp585', 'id': 'climatedata_CMIP6_ScenarioMIP_NorESM2-LM_ssp585_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'fdd

INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'fdd_380', 'experiment': 'ssp585', 'id': 'climatedata_CMIP6_ScenarioMIP_HadGEM3-GC31-LL_ssp585_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'fdd_380', 'experiment': 'ssp245', 'id': 'climatedata_CMIP6_ScenarioMIP_HadGEM3-GC31-LL_ssp245_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'fdd_380', 'experiment': 'ssp585', 'id': 'climatedata_CMIP6_ScenarioMIP_MPI-ESM1-2-HR_ssp585_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'fdd_380', 'experiment': 'ssp585', 'id': 'climatedata_CMIP6_ScenarioMIP_BCC-CSM2-MR_ssp585_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'v


--> The keys in the returned dictionary of datasets are constructed as follows:
	'id.domain.processing_level.xrfreq'


...

INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'heat_wave_total_length_20_30', 'experiment': 'ssp245', 'id': 'climatedata_CMIP6_ScenarioMIP_MPI-ESM1-2-LR_ssp245_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'heat_wave_total_length_20_30', 'experiment': 'ssp585', 'id': 'climatedata_CMIP6_ScenarioMIP_CMCC-ESM2_ssp585_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'heat_wave_total_length_20_30', 'experiment': 'ssp585', 'id': 'climatedata_CMIP6_ScenarioMIP_MPI-ESM1-2-LR_ssp585_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'heat_wave_total_length_20_30', 'experiment': 'ssp585', 'id': 'climatedata_CMIP6_ScenarioMIP_MRI-ESM2-0_ssp585_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INF

INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'heat_wave_total_length_20_30', 'experiment': 'ssp245', 'id': 'climatedata_CMIP6_ScenarioMIP_GFDL-ESM4_ssp245_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'heat_wave_total_length_20_30', 'experiment': 'ssp585', 'id': 'climatedata_CMIP6_ScenarioMIP_INM-CM4-8_ssp585_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'heat_wave_total_length_20_30', 'experiment': 'ssp245', 'id': 'climatedata_CMIP6_ScenarioMIP_IPSL-CM6A-LR_ssp245_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'heat_wave_total_length_20_30', 'experiment': 'ssp245', 'id': 'climatedata_CMIP6_ScenarioMIP_BCC-CSM2-MR_ssp245_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xs


--> The keys in the returned dictionary of datasets are constructed as follows:
	'id.domain.processing_level.xrfreq'


INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'fdd_380_273', 'experiment': 'ssp245', 'id': 'climatedata_CMIP6_ScenarioMIP_CNRM-ESM2-1_ssp245_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'fdd_380_273', 'experiment': 'ssp585', 'id': 'climatedata_CMIP6_ScenarioMIP_KIOST-ESM_ssp585_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'fdd_380_273', 'experiment': 'ssp245', 'id': 'climatedata_CMIP6_ScenarioMIP_MPI-ESM1-2-HR_ssp245_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'fdd_380_273', 'experiment': 'ssp245', 'id': 'climatedata_CMIP6_ScenarioMIP_MPI-ESM1-2-LR_ssp245_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatol

INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'fdd_380_273', 'experiment': 'ssp585', 'id': 'climatedata_CMIP6_ScenarioMIP_KACE-1-0-G_ssp585_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'fdd_380_273', 'experiment': 'ssp585', 'id': 'climatedata_CMIP6_ScenarioMIP_INM-CM5-0_ssp585_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'fdd_380_273', 'experiment': 'ssp245', 'id': 'climatedata_CMIP6_ScenarioMIP_CNRM-CM6-1_ssp245_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 'variable': 'fdd_380_273', 'experiment': 'ssp245', 'id': 'climatedata_CMIP6_ScenarioMIP_UKESM1-0-LL_ssp245_CAN-PCIC', 'bias_adjust_project': 'climatedata'}
INFO:xscen.catalog:An entry exists for: {'processing_level': 'climatology', 

In [4]:
# delta
with Client(n_workers=5, threads_per_worker=4,dashboard_address= 6787, memory_limit="6GB",local_directory= CONFIG['paths']['local_directory'] ):
    for name, ind in  chain(mod.iter_indicators(), zip(['fdd_380_273'], [mod.fdd_380])):
        ds_dict = pcat.search(processing_level="climatology",bias_adjust_project='climatedata',
                              variable=name).to_dataset_dict(**tdd)
        for ds_input in ds_dict.values():
            if not pcat.exists_in_cat(processing_level=['abs-delta', '30ymean'],
                                      variable=f"{name}_delta_1991_2020",
                                      id= ds_input.attrs['cat:id']):

                ds_delta = xs.aggregate.compute_deltas(ds=ds_input,
                                                       reference_horizon= "1991-2020",
                                                       kind="+",
                                                       to_level='abs-delta')
                display(ds_delta)
                var=[x for x in ds_delta.data_vars][0]
                filename = Path(CONFIG['paths']['indicators'].format(var=var,**xs.utils.get_cat_attrs(ds_delta)))
                xs.save_to_zarr(ds_delta, filename, mode="o")
                pcat.update_from_ds(ds=ds_delta, path=filename)

/exec/jlavoie/.conda/espo-g/lib/python3.9/site-packages/distributed/node.py:182: UserWarning: Port 6787 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 41747 instead
INFO:distributed.scheduler:State start
INFO:distributed.scheduler:  Scheduler at:     tcp://127.0.0.1:38182
INFO:distributed.scheduler:  dashboard at:           127.0.0.1:41747
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:38343'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:43940'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:44626'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:38350'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:42830'
INFO:distributed.scheduler:Register worker <WorkerState 'tcp://127.0.0.1:41139', name: 2, status: init, memory: 0, processing: 0>
INFO:distributed.scheduler:Starting worker compute stream, tcp://127.0.0.1:41139
INFO:distributed.core:Starting established c


--> The keys in the returned dictionary of datasets are constructed as follows:
	'id.domain.processing_level.xrfreq'


INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'fdd_380_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_MPI-ESM1-2-LR_ssp245_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'fdd_380_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_CNRM-CM6-1_ssp245_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'fdd_380_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_CMCC-ESM2_ssp245_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'fdd_380_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_FGOALS-g3_ssp585_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'fdd_380_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_CanESM5_ssp585_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'

INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'fdd_380_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_KACE-1-0-G_ssp245_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'fdd_380_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_EC-Earth3-Veg_ssp245_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'fdd_380_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_GFDL-ESM4_ssp585_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'fdd_380_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_UKESM1-0-LL_ssp585_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'fdd_380_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_INM-CM5-0_ssp245_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for


--> The keys in the returned dictionary of datasets are constructed as follows:
	'id.domain.processing_level.xrfreq'


...

INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'heat_wave_total_length_20_30_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_KACE-1-0-G_ssp585_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'heat_wave_total_length_20_30_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_CNRM-ESM2-1_ssp245_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'heat_wave_total_length_20_30_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_ACCESS-ESM1-5_ssp585_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'heat_wave_total_length_20_30_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_KACE-1-0-G_ssp245_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'heat_wave_total_length_20_30_delta_1991_2020

INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'heat_wave_total_length_20_30_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_MPI-ESM1-2-HR_ssp585_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'heat_wave_total_length_20_30_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_TaiESM1_ssp245_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'heat_wave_total_length_20_30_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_KIOST-ESM_ssp585_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'heat_wave_total_length_20_30_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_INM-CM4-8_ssp245_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'heat_wave_total_length_20_30_delta_1991_2020', 'id


--> The keys in the returned dictionary of datasets are constructed as follows:
	'id.domain.processing_level.xrfreq'


INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'fdd_380_273_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_MPI-ESM1-2-LR_ssp585_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'fdd_380_273_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_CNRM-CM6-1_ssp585_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'fdd_380_273_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_MIROC6_ssp585_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'fdd_380_273_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_CNRM-ESM2-1_ssp585_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'fdd_380_273_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_INM-CM5-0_ssp585_CAN-PCIC'}
INFO:xscen.catalog:An

INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'fdd_380_273_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_IPSL-CM6A-LR_ssp585_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'fdd_380_273_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_KACE-1-0-G_ssp585_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'fdd_380_273_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_BCC-CSM2-MR_ssp245_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'fdd_380_273_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_MIROC6_ssp245_CAN-PCIC'}
INFO:xscen.catalog:An entry exists for: {'processing_level': ['abs-delta', '30ymean'], 'variable': 'fdd_380_273_delta_1991_2020', 'id': 'climatedata_CMIP6_ScenarioMIP_EC-Earth3_ssp585_CAN-PCIC'}
INFO:xscen.catalog:An 

In [5]:
# ensemble

# one ensemble (file) per level, per xrfreq, per variable, per experiment
for processing_level in ['indicators','climatology','abs-delta']:
    for variable, ind in chain(mod.iter_indicators(), zip(['fdd_380_273'], [mod.fdd_380])):
        if processing_level=='abs-delta':
            variable=variable+'_delta_1991_2020'
        ind_df = pcat.search(processing_level=processing_level,bias_adjust_project='climatedata',
                            variable=variable).df
        # iterate through available xrfreq, exp and variables
        for experiment in ind_df.experiment.unique():
            for xrfreq in ind_df.xrfreq.unique():

                ind_dict = pcat.search( processing_level=processing_level,
                                        experiment=experiment,
                                        xrfreq=xrfreq,
                                        bias_adjust_project='climatedata',
                                        variable=variable).to_dataset_dict(
                    #**tdd
                    **{'xarray_open_kwargs':{'decode_timedelta': False, 'chunks':{'time':-1}}}
                )

                if not pcat.exists_in_cat(
                        processing_level= f'ensemble-{processing_level}',
                        xrfreq=xrfreq,
                        experiment=experiment,
                        bias_adjust_project='climatedata',
                        variable=variable+ "_p50",
                ):
                    with ProgressBar():

                        ens = xs.ensembles.ensemble_stats(
                            datasets=ind_dict,
                            to_level= f'ensemble-{processing_level}',
                            statistics={'ensemble_percentiles':{'split': True}},
                            common_attrs_only= True,
                            create_kwargs={'chunks':{'horizon': -1}},
                        )

                        ens.attrs['cat:variable']= xs.catalog.parse_from_ds(ens, ["variable"])["variable"]
                        display(ens)

                        filename = Path(CONFIG['paths']['indicators'].format(var = variable,
                                                                             **xs.utils.get_cat_attrs(ens)))
                        xs.save_to_zarr(ens, filename, mode="o", rechunk={'time':-1})
                        pcat.update_from_ds(ds=ens, path=filename)


--> The keys in the returned dictionary of datasets are constructed as follows:
	'id.domain.processing_level.xrfreq'


INFO:xscen.catalog:An entry exists for: {'processing_level': 'ensemble-indicators', 'xrfreq': 'AS-JUL', 'experiment': 'ssp245', 'bias_adjust_project': 'climatedata', 'variable': 'fdd_380_p50'}



--> The keys in the returned dictionary of datasets are constructed as follows:
	'id.domain.processing_level.xrfreq'


INFO:xscen.catalog:An entry exists for: {'processing_level': 'ensemble-indicators', 'xrfreq': 'AS-JUL', 'experiment': 'ssp585', 'bias_adjust_project': 'climatedata', 'variable': 'fdd_380_p50'}



--> The keys in the returned dictionary of datasets are constructed as follows:
	'id.domain.processing_level.xrfreq'


...

INFO:xscen.catalog:An entry exists for: {'processing_level': 'ensemble-abs-delta', 'xrfreq': 'AS-JAN', 'experiment': 'ssp585', 'bias_adjust_project': 'climatedata', 'variable': 'heat_wave_total_length_20_30_delta_1991_2020_p50'}



--> The keys in the returned dictionary of datasets are constructed as follows:
	'id.domain.processing_level.xrfreq'


INFO:xscen.catalog:An entry exists for: {'processing_level': 'ensemble-abs-delta', 'xrfreq': 'AS-JUL', 'experiment': 'ssp585', 'bias_adjust_project': 'climatedata', 'variable': 'fdd_380_273_delta_1991_2020_p50'}



--> The keys in the returned dictionary of datasets are constructed as follows:
	'id.domain.processing_level.xrfreq'


INFO:xscen.catalog:An entry exists for: {'processing_level': 'ensemble-abs-delta', 'xrfreq': 'AS-JUL', 'experiment': 'ssp245', 'bias_adjust_project': 'climatedata', 'variable': 'fdd_380_273_delta_1991_2020_p50'}


# fdd_380_273
 change nan in march 31st

In [ ]:
with Client(n_workers=4, threads_per_worker=4,dashboard_address= 6785, memory_limit="6GB",local_directory= CONFIG['paths']['local_directory'] ):

    dict_input=pcat_espo.search(variable='fdd_380', processing_level='indicators',
                           experiment=['ssp245', 'ssp370']).to_dataset_dict(**tdd)
    for id, ds, in dict_input.items():
        if not pcat_espo.exists_in_cat(processing_level='indicators',
                          variable='fdd_380_273',
                          xrfreq='AS-JUL',
                          source=ds.attrs['cat:source'],
                          experiment=ds.attrs['cat:experiment'],
                          bias_adjust_project='climatedata'): 
            
            out= ds.where(~ds.isnull(), other=273).rename(dict(fdd_380='fdd_380_273')) # march 31st = doy 90 = 273 since 07-01
            filename = Path(CONFIG['paths']['indicators'].format(var = 'fdd_380_273',**xs.utils.get_cat_attrs(out)))
            xs.save_to_zarr(out, filename, mode="o",rechunk={'time': -1})
            pcat_espo.update_from_ds(ds=out, path=filename)

In [37]:
# CD
with Client(n_workers=4, threads_per_worker=4,dashboard_address= 6785, memory_limit="6GB",local_directory= CONFIG['paths']['local_directory'] ):

    dict_input=pcat.search(variable='fdd_380', processing_level='indicators',bias_adjust_project='climatedata',
                           experiment=['ssp245', 'ssp585']).to_dataset_dict(**tdd)
    for id, ds, in dict_input.items():
        if not pcat.exists_in_cat(processing_level='indicators',
                          variable='fdd_380_273',
                          xrfreq='AS-JUL',
                          source=ds.attrs['cat:source'],
                          experiment=ds.attrs['cat:experiment'],
                          bias_adjust_project='climatedata'): 
            
            out= ds.where(~ds.isnull(), other=273).rename(dict(fdd_380='fdd_380_273')) # march 31st = doy 90 = 273 since 07-01
            filename = Path(CONFIG['paths']['indicators'].format(var = 'fdd_380_273',**xs.utils.get_cat_attrs(out)))
            xs.save_to_zarr(out, filename, mode="o",rechunk={'time': -1})
            pcat.update_from_ds(ds=out, path=filename)
        #     plt.figure()
        #     ds['fdd_380'].sel(time='2071').plot()
        #     plt.figure()
        #     new_ds['fdd_380_273'].sel(time='2071').plot()
        #     display(new_ds)

INFO:distributed.scheduler:State start
INFO:distributed.scheduler:  Scheduler at:     tcp://127.0.0.1:37349
INFO:distributed.scheduler:  dashboard at:            127.0.0.1:6785
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:45745'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:34395'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:40401'
INFO:distributed.nanny:        Start Nanny at: 'tcp://127.0.0.1:34834'
INFO:distributed.scheduler:Register worker <WorkerState 'tcp://127.0.0.1:37878', name: 0, status: init, memory: 0, processing: 0>
INFO:distributed.scheduler:Starting worker compute stream, tcp://127.0.0.1:37878
INFO:distributed.core:Starting established connection to tcp://127.0.0.1:60836
INFO:distributed.scheduler:Register worker <WorkerState 'tcp://127.0.0.1:45620', name: 1, status: init, memory: 0, processing: 0>
INFO:distributed.scheduler:Starting worker compute stream, tcp://127.0.0.1:45620
INFO:distributed.core:Starting establi


--> The keys in the returned dictionary of datasets are constructed as follows:
	'id.domain.processing_level.xrfreq'


INFO:xscen.catalog:File format not specified. Adding it as 'zarr' based on file name.
INFO:xscen.catalog:File format not specified. Adding it as 'zarr' based on file name.
INFO:xscen.catalog:File format not specified. Adding it as 'zarr' based on file name.
INFO:xscen.catalog:File format not specified. Adding it as 'zarr' based on file name.
INFO:xscen.catalog:File format not specified. Adding it as 'zarr' based on file name.
INFO:xscen.catalog:File format not specified. Adding it as 'zarr' based on file name.
INFO:xscen.catalog:File format not specified. Adding it as 'zarr' based on file name.
INFO:xscen.catalog:File format not specified. Adding it as 'zarr' based on file name.
INFO:xscen.catalog:File format not specified. Adding it as 'zarr' based on file name.
INFO:xscen.catalog:File format not specified. Adding it as 'zarr' based on file name.
INFO:xscen.catalog:File format not specified. Adding it as 'zarr' based on file name.
INFO:xscen.catalog:File format not specified. Adding i